In [1]:
import tensorflow as tf
import pandas as pd

from stable_baselines.common.policies import MlpLnLstmPolicy
from stable_baselines import PPO2

from tensortrade.strategies import StableBaselinesTradingStrategy
from tensortrade.environments import TradingEnvironment
from tensortrade.rewards import RiskAdjustedReturns
from tensortrade.actions import PairCriteriaSizeActions
from tensortrade.instruments import Quantity, TradingPair, BTC, USD
from tensortrade.wallets import Wallet, Portfolio
from tensortrade.exchanges.simulated import SimulatedExchange
from tensortrade.features.stationarity import FractionalDifference
from tensortrade.features.scalers import MinMaxNormalizer
from tensortrade.features import FeaturePipeline

WINDOW_SIZE = 20
PRICE_COLUMN = 'close'

normalize = MinMaxNormalizer(inplace=True)
difference = FractionalDifference(difference_order=0.6, inplace=True)
feature_pipeline = FeaturePipeline(steps=[normalize, difference])

action_scheme = PairCriteriaSizeActions(TradingPair(USD, BTC))
reward_scheme = RiskAdjustedReturns(return_algorithm="sharpe")

csv_file = tf.keras.utils.get_file(
    'Coinbase_BTCUSD_1h.csv', 'https://www.cryptodatadownload.com/cdd/Coinbase_BTCUSD_1h.csv')
ohlcv_data = pd.read_csv(csv_file, skiprows=1, index_col="Date")
ohlcv_data.columns = map(str.lower, ohlcv_data.columns)
ohlcv_data = ohlcv_data.rename(columns={'volume btc': 'volume'})

# ohlcv_data = pd.read_csv('./data/updateOHLCdata_master.csv')
ohlcv_data = ohlcv_data.iloc[0:10000]

exchange = SimulatedExchange(base_instrument=USD,
                             data_frame=ohlcv_data,
                             price_column=PRICE_COLUMN,
                             window_size=WINDOW_SIZE,
                             pretransform=True)

exchange.reset()

quantity_usd = Quantity(USD, 10000)
quantity_btc = Quantity(BTC, 0)

wallet_usd = Wallet(exchange, quantity_usd)
wallet_btc = Wallet(exchange, quantity_btc)

portfolio = Portfolio(base_instrument=USD)

portfolio.add(wallet_usd)
portfolio.add(wallet_btc)

exchange.portfolio = portfolio

exchange.reset()

print('Transformed Data:')
print(exchange.observation_columns)

model = PPO2
policy = MlpLnLstmPolicy
params = {'learning_rate': 1e-5,
          'nminibatches': 1,
          'verbose': 2}

environment = TradingEnvironment(exchange=exchange,
                                 action_scheme=action_scheme,
                                 reward_scheme=reward_scheme,
                                 feature_pipeline=feature_pipeline)

strategy = StableBaselinesTradingStrategy(environment=environment,
                                          model=model,
                                          policy=policy,
                                          model_kwargs=params)

performance = strategy.run(steps=10000)

W1208 11:15:06.542135 4758773184 deprecation_wrapper.py:119] From /usr/local/lib/python3.7/site-packages/tensorforce/core/module.py:31: The name tf.enable_resource_variables is deprecated. Please use tf.compat.v1.enable_resource_variables instead.

W1208 11:15:06.558073 4758773184 deprecation_wrapper.py:119] From /usr/local/lib/python3.7/site-packages/tensorforce/core/optimizers/tf_optimizer.py:46: The name tf.train.AdadeltaOptimizer is deprecated. Please use tf.compat.v1.train.AdadeltaOptimizer instead.

W1208 11:15:06.559183 4758773184 deprecation_wrapper.py:119] From /usr/local/lib/python3.7/site-packages/tensorforce/core/optimizers/tf_optimizer.py:47: The name tf.train.AdagradOptimizer is deprecated. Please use tf.compat.v1.train.AdagradOptimizer instead.

W1208 11:15:06.560186 4758773184 deprecation_wrapper.py:119] From /usr/local/lib/python3.7/site-packages/tensorforce/core/optimizers/tf_optimizer.py:48: The name tf.train.AdamOptimizer is deprecated. Please use tf.compat.v1.train

Transformed Data:
Index(['open', 'high', 'low', 'close', 'volume', 'volume usd'], dtype='object')
performance      step     net_worth       USD       BTC
step    0  10000.000000  10000.00  0.000000
step    1   9980.761822   6676.64  0.285084
Reward:  nan
performance      step     net_worth       USD       BTC
step    0  10000.000000  10000.00  0.000000
step    1   9980.761822   6676.64  0.285084
step    2   9983.447612   5843.31  0.357216
Reward:  -0.5338588693721761
performance      step     net_worth       USD       BTC
step    0  10000.000000  10000.00  0.000000
step    1   9980.761822   6676.64  0.285084
step    2   9983.447612   5843.31  0.357216
step    3   9983.445917   5843.43  0.357206
Reward:  -0.4614607287664359
performance      step     net_worth       USD       BTC
step    0  10000.000000  10000.00  0.000000
step    1   9980.761822   6676.64  0.285084
step    2   9983.447612   5843.31  0.357216
step    3   9983.445917   5843.43  0.357206
step    4   9983.445150   5843.55  

performance      step     net_worth       USD       BTC
step    0  10000.000000  10000.00  0.000000
step    1   9980.761822   6676.64  0.285084
step    2   9983.447612   5843.31  0.357216
step    3   9983.445917   5843.43  0.357206
step    4   9983.445150   5843.55  0.357195
step    5   9983.444835   5843.56  0.357195
step    6   9987.632662   5605.08  0.378132
step    7   9987.632727   5605.10  0.378131
step    8   9984.093316   5306.80  0.403563
step    9   9979.331645   5008.08  0.428926
step   10   9979.331923   5008.13  0.428922
step   11   9979.328504   5007.97  0.428935
step   12   9979.328537   5007.98  0.428934
step   13   9979.328570   5007.99  0.428933
step   14   9979.326422   5007.90  0.428941
step   15   9979.326487   5007.92  0.428939
step   16   9979.326636   5007.93  0.428938
step   17   9979.325661   5007.88  0.428943
step   18   9979.326157   5007.89  0.428942
step   19   9979.326654   5007.90  0.428941
step   20   9979.329385   5007.92  0.428940
step   21   9979.330

performance      step     net_worth       USD       BTC
step    0  10000.000000  10000.00  0.000000
step    1   9980.761822   6676.64  0.285084
step    2   9983.447612   5843.31  0.357216
step    3   9983.445917   5843.43  0.357206
step    4   9983.445150   5843.55  0.357195
step    5   9983.444835   5843.56  0.357195
step    6   9987.632662   5605.08  0.378132
step    7   9987.632727   5605.10  0.378131
step    8   9984.093316   5306.80  0.403563
step    9   9979.331645   5008.08  0.428926
step   10   9979.331923   5008.13  0.428922
step   11   9979.328504   5007.97  0.428935
step   12   9979.328537   5007.98  0.428934
step   13   9979.328570   5007.99  0.428933
step   14   9979.326422   5007.90  0.428941
step   15   9979.326487   5007.92  0.428939
step   16   9979.326636   5007.93  0.428938
step   17   9979.325661   5007.88  0.428943
step   18   9979.326157   5007.89  0.428942
step   19   9979.326654   5007.90  0.428941
step   20   9979.329385   5007.92  0.428940
step   21   9979.330

Reward:  -0.11144939253591431
performance      step     net_worth       USD       BTC
step    0  10000.000000  10000.00  0.000000
step    1   9980.761822   6676.64  0.285084
step    2   9983.447612   5843.31  0.357216
step    3   9983.445917   5843.43  0.357206
step    4   9983.445150   5843.55  0.357195
...   ...           ...       ...       ...
step   77   9979.326961   5007.71  0.428957
step   78   9979.326961   5007.71  0.428957
step   79   9979.326961   5007.71  0.428957
step   80   9979.326961   5007.71  0.428957
step   81   9979.326961   5007.71  0.428957

[82 rows x 4 columns]
Reward:  -0.11075935149274306
performance      step     net_worth       USD       BTC
step    0  10000.000000  10000.00  0.000000
step    1   9980.761822   6676.64  0.285084
step    2   9983.447612   5843.31  0.357216
step    3   9983.445917   5843.43  0.357206
step    4   9983.445150   5843.55  0.357195
...   ...           ...       ...       ...
step   78   9979.326961   5007.71  0.428957
step   79   9

...

performance       step     net_worth       USD       BTC
step     0  10000.000000  10000.00  0.000000
step     1   9980.761822   6676.64  0.285084
step     2   9983.447612   5843.31  0.357216
step     3   9983.445917   5843.43  0.357206
step     4   9983.445150   5843.55  0.357195
...    ...           ...       ...       ...
step  9912   9979.326961   5007.71  0.428957
step  9913   9979.326961   5007.71  0.428957
step  9914   9979.326961   5007.71  0.428957
step  9915   9979.326961   5007.71  0.428957
step  9916   9979.326961   5007.71  0.428957

[9917 rows x 4 columns]
Reward:  -0.010010861752477868
performance       step     net_worth       USD       BTC
step     0  10000.000000  10000.00  0.000000
step     1   9980.761822   6676.64  0.285084
step     2   9983.447612   5843.31  0.357216
step     3   9983.445917   5843.43  0.357206
step     4   9983.445150   5843.55  0.357195
...    ...           ...       ...       ...
step  9913   9979.326961   5007.71  0.428957
step  9914   9979.32

performance       step     net_worth       USD       BTC
step     0  10000.000000  10000.00  0.000000
step     1   9980.761822   6676.64  0.285084
step     2   9983.447612   5843.31  0.357216
step     3   9983.445917   5843.43  0.357206
step     4   9983.445150   5843.55  0.357195
...    ...           ...       ...       ...
step  9933   9979.326961   5007.71  0.428957
step  9934   9979.326961   5007.71  0.428957
step  9935   9979.326961   5007.71  0.428957
step  9936   9979.326961   5007.71  0.428957
step  9937   9979.326961   5007.71  0.428957

[9938 rows x 4 columns]
Reward:  -0.010000278117952796
performance       step     net_worth       USD       BTC
step     0  10000.000000  10000.00  0.000000
step     1   9980.761822   6676.64  0.285084
step     2   9983.447612   5843.31  0.357216
step     3   9983.445917   5843.43  0.357206
step     4   9983.445150   5843.55  0.357195
...    ...           ...       ...       ...
step  9934   9979.326961   5007.71  0.428957
step  9935   9979.32

performance       step     net_worth       USD       BTC
step     0  10000.000000  10000.00  0.000000
step     1   9980.761822   6676.64  0.285084
step     2   9983.447612   5843.31  0.357216
step     3   9983.445917   5843.43  0.357206
step     4   9983.445150   5843.55  0.357195
...    ...           ...       ...       ...
step  9954   9979.326961   5007.71  0.428957
step  9955   9979.326961   5007.71  0.428957
step  9956   9979.326961   5007.71  0.428957
step  9957   9979.326961   5007.71  0.428957
step  9958   9979.326961   5007.71  0.428957

[9959 rows x 4 columns]
Reward:  -0.009989727980143024
performance       step     net_worth       USD       BTC
step     0  10000.000000  10000.00  0.000000
step     1   9980.761822   6676.64  0.285084
step     2   9983.447612   5843.31  0.357216
step     3   9983.445917   5843.43  0.357206
step     4   9983.445150   5843.55  0.357195
...    ...           ...       ...       ...
step  9955   9979.326961   5007.71  0.428957
step  9956   9979.32

performance       step     net_worth       USD       BTC
step     0  10000.000000  10000.00  0.000000
step     1   9980.761822   6676.64  0.285084
step     2   9983.447612   5843.31  0.357216
step     3   9983.445917   5843.43  0.357206
step     4   9983.445150   5843.55  0.357195
...    ...           ...       ...       ...
step  9973   9979.326961   5007.71  0.428957
step  9974   9979.326961   5007.71  0.428957
step  9975   9979.326961   5007.71  0.428957
step  9976   9979.326961   5007.71  0.428957
step  9977   9979.326961   5007.71  0.428957

[9978 rows x 4 columns]
Reward:  -0.009980211333611377
performance       step     net_worth       USD       BTC
step     0  10000.000000  10000.00  0.000000
step     1   9980.761822   6676.64  0.285084
step     2   9983.447612   5843.31  0.357216
step     3   9983.445917   5843.43  0.357206
step     4   9983.445150   5843.55  0.357195
...    ...           ...       ...       ...
step  9974   9979.326961   5007.71  0.428957
step  9975   9979.32

performance       step     net_worth       USD       BTC
step     0  10000.000000  10000.00  0.000000
step     1   9980.761822   6676.64  0.285084
step     2   9983.447612   5843.31  0.357216
step     3   9983.445917   5843.43  0.357206
step     4   9983.445150   5843.55  0.357195
...    ...           ...       ...       ...
step  9992   9979.326961   5007.71  0.428957
step  9993   9979.326961   5007.71  0.428957
step  9994   9979.326961   5007.71  0.428957
step  9995   9979.326961   5007.71  0.428957
step  9996   9979.326961   5007.71  0.428957

[9997 rows x 4 columns]
Reward:  -0.00997072183326854
performance       step     net_worth       USD       BTC
step     0  10000.000000  10000.00  0.000000
step     1   9980.761822   6676.64  0.285084
step     2   9983.447612   5843.31  0.357216
step     3   9983.445917   5843.43  0.357206
step     4   9983.445150   5843.55  0.357195
...    ...           ...       ...       ...
step  9993   9979.326961   5007.71  0.428957
step  9994   9979.326